### 네이버 리뷰로 긍정부정 판단

#### 1. 전처리

In [1]:
import urllib.request
urllib.request.urlretrieve("https://raw.githubusercontent.com/e9t/nsmc/master/ratings_train.txt",
filename="./data/ratings_train.txt")
urllib.request.urlretrieve("https://raw.githubusercontent.com/e9t/nsmc/master/ratings_test.txt",
filename="./data/ratings_test.txt")

('./data/ratings_test.txt', <http.client.HTTPMessage at 0x2444f2b7d30>)

In [2]:
import pandas as pd
from tensorflow.keras.preprocessing.text import text_to_word_sequence


#데이터 불러오기
train_data = pd.read_table('./data/ratings_train.txt')
test_data = pd.read_table('./data/ratings_test.txt')

print(train_data)
print(test_data)

              id                                           document  label
0        9976970                                아 더빙.. 진짜 짜증나네요 목소리      0
1        3819312                  흠...포스터보고 초딩영화줄....오버연기조차 가볍지 않구나      1
2       10265843                                  너무재밓었다그래서보는것을추천한다      0
3        9045019                      교도소 이야기구먼 ..솔직히 재미는 없다..평점 조정      0
4        6483659  사이몬페그의 익살스런 연기가 돋보였던 영화!스파이더맨에서 늙어보이기만 했던 커스틴 ...      1
...          ...                                                ...    ...
149995   6222902                                인간이 문제지.. 소는 뭔죄인가..      0
149996   8549745                                      평점이 너무 낮아서...      1
149997   9311800                    이게 뭐요? 한국인은 거들먹거리고 필리핀 혼혈은 착하다?      0
149998   2376369                        청춘 영화의 최고봉.방황과 우울했던 날들의 자화상      1
149999   9619869                           한국 영화 최초로 수간하는 내용이 담긴 영화      0

[150000 rows x 3 columns]
            id                                           document  label


In [3]:
# 같은 리뷰 제거
train_data.drop_duplicates(subset=['document'], inplace=True)
test_data.drop_duplicates(subset=['document'], inplace=True)
print(len(train_data))
print(len(test_data))

146183
49158


In [4]:
print("train data")
#결측치 확인
print(train_data.isnull().sum())
print()
# 결측치가 있는 행 제거
train_data = train_data.dropna(subset=['document'])

# 결측치가 있는 행을 제거한 후 결측치 개수 확인
print(train_data.isnull().sum())

print("test data")

#결측치 확인
print(test_data.isnull().sum())
print()
# 결측치가 있는 행 제거
test_data = test_data.dropna(subset=['document'])

# 결측치가 있는 행을 제거한 후 결측치 개수 확인
print(test_data.isnull().sum())


train data
id          0
document    1
label       0
dtype: int64

id          0
document    0
label       0
dtype: int64
test data
id          0
document    1
label       0
dtype: int64

id          0
document    0
label       0
dtype: int64


In [5]:
# import numpy as np
# import re

# # 한글을 제외한 문자를 '' 로 변경
# train_data['document'] = train_data['document'].str.replace(r'[^ㄱ-ㅎㅏ-ㅣ가-힣 " "]', 
#                                                           '', regex=True)
# # '' 를 np.nan  으로 변경 -> nan 을 제거
# train_data['document'].replace('', np.nan, inplace=True)
# train_data.dropna(inplace=True)

# print(len(train_data))

In [6]:
import numpy as np
import re

def remove_special_characters(text):
    # 정규표현식을 사용하여 특수문자 제거
    processed_text = re.sub(r'[^\w\s]', '', text)
    return processed_text

# 'document' 열에서 특수문자 제거
train_data['document'] = train_data['document'].apply(remove_special_characters)
test_data['document'] = test_data['document'].apply(remove_special_characters)

# 처리 후 결과 출력
print(len(train_data))
print(len(test_data))

146182
49157


In [7]:
# train set, test set 분리

X_train = train_data['document']
y_train = train_data['label']
X_test = test_data['document']
y_test = test_data['label']

#### 모델 학습

In [8]:
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.layers import Dense, Dropout, Activation, Embedding, LSTM, Conv1D, MaxPool1D
from tensorflow.keras.datasets import imdb
from tensorflow.keras.preprocessing import sequence
from tensorflow.keras.callbacks import EarlyStopping

import numpy as np
import matplotlib.pyplot as plt

In [9]:
#토큰화
token = Tokenizer()
token.fit_on_texts(X_train)
token.fit_on_texts(X_test)
print(token.word_index)

x1 = token.texts_to_sequences(X_train)
x2 = token.texts_to_sequences(X_test)

{'영화': 1, '너무': 2, '정말': 3, '진짜': 4, '이': 5, '왜': 6, '그냥': 7, '더': 8, '이런': 9, '수': 10, '영화를': 11, '잘': 12, '다': 13, '보고': 14, '좀': 15, '영화는': 16, '그': 17, '영화가': 18, '본': 19, '최고의': 20, '봤는데': 21, '내가': 22, '없는': 23, 'ㅋㅋ': 24, '이건': 25, '없다': 26, '이렇게': 27, '드라마': 28, '평점': 29, '이거': 30, '완전': 31, '있는': 32, '이게': 33, '참': 34, '좋은': 35, '아': 36, '평점이': 37, '다시': 38, '보는': 39, '연기': 40, '내': 41, '그리고': 42, '역시': 43, '많이': 44, '것': 45, '난': 46, '스토리': 47, '한': 48, '쓰레기': 49, '재밌게': 50, '최고': 51, '하는': 52, '없고': 53, '또': 54, '보면': 55, '꼭': 56, '가장': 57, 'ㅋㅋㅋ': 58, 'ㅠㅠ': 59, '아깝다': 60, '마지막': 61, '영화다': 62, '무슨': 63, 'ㅡㅡ': 64, '뭐': 65, 'ㅋ': 66, '볼': 67, '하지만': 68, '같은': 69, '작품': 70, '10점': 71, '끝까지': 72, '만든': 73, '안': 74, '솔직히': 75, '대한': 76, '봐도': 77, '넘': 78, '전혀': 79, '말이': 80, '영화의': 81, '별로': 82, '내내': 83, '지금': 84, '아주': 85, '같다': 86, 'ㅎㅎ': 87, '다른': 88, '뭔가': 89, '그래도': 90, '할': 91, '최악의': 92, '있다': 93, '좋다': 94, '하고': 95, '않고': 96, '하나': 97, '어떻게': 98, '재미': 99, '많은': 100, '연기가':

In [10]:
#패딩, 서로 다른 길이의 데이터를 4로 맞춤
padded_x1 = pad_sequences(x1,20)
padded_x2 = pad_sequences(x2,20)

In [11]:
#임베딩에 입력될 단어의 수를 지정
word_size = len(token.word_index)+1

In [12]:
print(len(X_train))
print(len(X_test))
print(len(y_train))
print(len(y_test))


146182
49157
146182
49157


In [13]:
#모델 설정
model = Sequential()
model.add(Embedding(word_size, 20)) #단어 임베딩
model.add(Dropout(0.5)) #노드 꺼줌(50%)
model.add(Conv1D(64,5,padding = 'valid', activation= 'relu', strides=1)) 
model.add(MaxPool1D(pool_size=4)) #maxpooling -> 25%로 줄어듦
model.add(LSTM(55)) #node수 
model.add(Dense(1))
model.add(Activation('sigmoid'))

In [14]:
model.compile(loss = 'binary_crossentropy', optimizer='adam', metrics=['accuracy'])

early_stopping_callback = EarlyStopping(monitor='val_loss', patience=3)

history = model.fit(padded_x1, y_train, batch_size=40, epochs=100, 
                    validation_split = 0.25, callbacks=[early_stopping_callback])

Epoch 1/100


ValueError: in user code:

    File "c:\Users\rhkr3\anaconda3\envs\py3.8\lib\site-packages\keras\engine\training.py", line 1284, in train_function  *
        return step_function(self, iterator)
    File "c:\Users\rhkr3\anaconda3\envs\py3.8\lib\site-packages\keras\engine\training.py", line 1268, in step_function  **
        outputs = model.distribute_strategy.run(run_step, args=(data,))
    File "c:\Users\rhkr3\anaconda3\envs\py3.8\lib\site-packages\keras\engine\training.py", line 1249, in run_step  **
        outputs = model.train_step(data)
    File "c:\Users\rhkr3\anaconda3\envs\py3.8\lib\site-packages\keras\engine\training.py", line 1050, in train_step
        y_pred = self(x, training=True)
    File "c:\Users\rhkr3\anaconda3\envs\py3.8\lib\site-packages\keras\utils\traceback_utils.py", line 70, in error_handler
        raise e.with_traceback(filtered_tb) from None

    ValueError: Exception encountered when calling layer 'conv1d' (type Conv1D).
    
    Negative dimension size cau

In [ ]:
print('Test Accuracy: %%.4f'%(model.evaluate(padded_x2, y_test)[1]))
y_vloss = history.history['val_loss']
y_loss = history.history['loss']

In [ ]:
x_len = np.arange(len(y_loss))
plt.plot(x_len, y_vloss, marker = '.', c='red', label= 'Testset_loss')
plt.plot(x_len, y_loss, marker = '.', c='blue', label= 'Trainset_loss')

plt.legend(loc= 'upper right')
plt.grid()
plt.xlabel('epoch')
plt.ylabel('loss')
plt.show()